In [2]:
import json
import logging
from kafka import KafkaProducer
import requests

In [3]:
KAFKA_BROKER = 'kafka1:9092'

class KafkaManager:
    def __init__(self, broker):
        try:
            self.producer = KafkaProducer(
                bootstrap_servers=broker,
                value_serializer=lambda v: json.dumps(v).encode('utf-8')
            )
            logging.info("Kafka Producer créé avec succès.")
        except Exception as e:
            logging.error(f"Erreur lors de la création du producer : {e}")
            raise

    def send_message(self, topic, message):
        try:
            self.producer.send(topic, message)
            logging.info(f"Message envoyé sur {topic}: {message}")
        except Exception as e:
            logging.error(f"Erreur lors de l'envoi du message sur {topic} : {e}")

    def flush(self):
        self.producer.flush()

    def close(self):
        self.producer.close()


In [4]:
def fetch_data_from_url(url):
    print("Requesting:", url)
    response = requests.get(url)
    if response.status_code == 200:
        try:
            return response.json()
        except ValueError:
            logging.error(f"Erreur: La réponse de {url} n'est pas au format JSON.")
            return None
    else:
        logging.error(f"Échec de la requête {url}: {response.status_code}")
        return None

def extract_fields(item, fields):
    return {field: item.get(field) for field in fields}

In [8]:
def send_data_to_kafka(kafka_manager, topic, data, fields, expected_type=list):
    messages = []
    if data is None:
        return messages

    # Déterminer la liste d'éléments à traiter
    if isinstance(data, list):
        items = data
    elif isinstance(data, dict) and 'results' in data:
        items = data.get('results', [])
    elif isinstance(data, dict) and expected_type == dict:
        items = [data]
    else:
        logging.warning(f"Type de données inattendu: {type(data)}")
        items = []

    for item in items:
        if isinstance(item, dict):
            message = extract_fields(item, fields)
            kafka_manager.send_message(topic, message)
            print(f"Sent message: {message}")
            messages.append(message)
        else:
            print(f"Warning: Expected dict but got {type(item)}")
    kafka_manager.flush()
    print(f"Sent {len(messages)} records to topic {topic}")
    return messages


In [ ]:
kafka_manager = KafkaManager(KAFKA_BROKER)

# 1. Import des arrêts
arrets_url = "https://open.tan.fr/ewp/arrets.json"
arrets_fields = ["codeLieu", "libelle", "distance", "ligne"]
arrets_data = fetch_data_from_url(arrets_url)
arrets_messages = send_data_to_kafka(kafka_manager, "arrets", arrets_data, arrets_fields)

# 2. Pour chaque arrêt, importer les temps d'attente et les horaires
attente_fields = ['sens', 'terminus', 'infotrafic', 'temps', 'dernierDepart', 'tempsReel', 'ligne', 'arret']
attente_url_template = "https://open.tan.fr/ewp/tempsattente.json/{}"
horaires_fields = ["ligne", "arret", "codeCouleur", "notes", "horaires", "prochainsHoraires", "plageDeService"]

if arrets_data and isinstance(arrets_data, list):
    for item in arrets_data:
        arret_code = item.get('codeLieu')
        attente_url = attente_url_template.format(arret_code)
        attente_data = fetch_data_from_url(attente_url)
        attente_messages = send_data_to_kafka(kafka_manager, "attente", attente_data, attente_fields, expected_type=list)
        # Pour chaque attente, envoyer les horaires correspondants
        for attente in attente_messages:
            codeArret = attente.get('arret', {}).get('codeArret')
            sens = attente.get('sens')
            num_ligne = attente.get('ligne', {}).get('numLigne')
            if codeArret and sens and num_ligne:
                horaire_url = "https://open.tan.fr/ewp/horairesarret.json/{}/{}/{}".format(codeArret, num_ligne, sens)
                horaire_data = fetch_data_from_url(horaire_url)
                # Ici, on attend un dictionnaire plutôt qu'une liste
                send_data_to_kafka(kafka_manager, "horaires", horaire_data, horaires_fields, expected_type=dict)

kafka_manager.close()


Requesting: https://open.tan.fr/ewp/arrets.json
Sent message: {'codeLieu': 'ABCH', 'libelle': 'Abbé Chérel', 'distance': None, 'ligne': [{'numLigne': '50'}, {'numLigne': '81'}, {'numLigne': '91'}, {'numLigne': 'NBI'}]}
Sent message: {'codeLieu': 'ABDU', 'libelle': 'Abel Durand', 'distance': None, 'ligne': [{'numLigne': 'C20'}, {'numLigne': 'NO'}]}
Sent message: {'codeLieu': 'ABLA', 'libelle': 'Avenue Blanche', 'distance': None, 'ligne': []}
Sent message: {'codeLieu': 'ABOL', 'libelle': 'Adrienne Bolland', 'distance': None, 'ligne': [{'numLigne': '77'}]}
Sent message: {'codeLieu': 'ACHA', 'libelle': 'Angle Chaillou', 'distance': None, 'ligne': [{'numLigne': '126'}, {'numLigne': '96'}]}
Sent message: {'codeLieu': 'ADBO', 'libelle': 'Audubon', 'distance': None, 'ligne': [{'numLigne': '101'}, {'numLigne': '141'}, {'numLigne': '91'}, {'numLigne': 'E1'}]}
Sent message: {'codeLieu': 'ADEL', 'libelle': 'Aimé Delrue', 'distance': None, 'ligne': [{'numLigne': '2'}, {'numLigne': '2B'}, {'numLigne

Sent message: {'sens': 1, 'terminus': 'Mendès France - Bellevue', 'infotrafic': True, 'temps': '', 'dernierDepart': 'false', 'tempsReel': 'false', 'ligne': {'numLigne': '81', 'typeLigne': 3}, 'arret': {'codeArret': 'ABCH1'}}
Sent message: {'sens': 1, 'terminus': 'Romanet', 'infotrafic': True, 'temps': '', 'dernierDepart': 'false', 'tempsReel': 'false', 'ligne': {'numLigne': '81', 'typeLigne': 3}, 'arret': {'codeArret': 'ABCH1'}}
Sent message: {'sens': 2, 'terminus': 'Gare Maritime', 'infotrafic': True, 'temps': '11mn', 'dernierDepart': 'false', 'tempsReel': 'true', 'ligne': {'numLigne': '81', 'typeLigne': 3}, 'arret': {'codeArret': 'ABCH2'}}
Sent 3 records to topic attente
Requesting: https://open.tan.fr/ewp/horairesarret.json/ABCH1/81/1
Sent message: {'ligne': {'numLigne': '81', 'typeligne': 3, 'directionSens1': 'Mendès France - Bellevue', 'directionSens2': 'Gare Maritime', 'accessible': '1', 'etatTrafic': 1}, 'arret': {'codeArret': 'ABCH1', 'libelle': 'Abbé Chérel', 'accessible': Tru

Sent message: {'grp_identifiant': '137', 'grp_nom': 'P+R Haluchère 2', 'grp_statut': 5, 'grp_disponible': 132, 'grp_exploitation': 155, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T15:45:41+00:00', 'idobj': '4764', 'location': {'lon': -1.5249751929999888, 'lat': 47.250230052000006}, 'disponibilite': 132.0}
Sent message: {'grp_identifiant': '138', 'grp_nom': 'P+R Le Cardo', 'grp_statut': 2, 'grp_disponible': 173, 'grp_exploitation': 206, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T15:45:41+00:00', 'idobj': '3189', 'location': {'lon': -1.584511976999977, 'lat': 47.262502085999984}, 'disponibilite': 173.0}
Sent message: {'grp_identifiant': '155', 'grp_nom': 'P+R Porte de Vertou 1', 'grp_statut': 5, 'grp_disponible': 181, 'grp_exploitation': 215, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T15:45:41+00:00', 'idobj': '5531', 'location': {'lon': -1.5058091440000112, 'lat': 47.180393442000025}, 'disponibilite': 181.0}
Sent message: {'grp_identifiant': '135', 'grp_nom': 'P+R François

Sent message: {'number': 1011, 'name': '01011 - BORNE TEST NANTES 1', 'address': 'Borne test 1', 'position': {'lon': -1.5575, 'lat': 47.19504}, 'banking': 'False', 'bonus': 'False', 'status': 'OPEN', 'contract_name': 'nantes', 'bike_stands': 0, 'available_bike_stands': 0, 'available_bikes': 0, 'last_update': '2022-05-23T14:41:50+00:00'}
Sent message: {'number': 1012, 'name': '01012 - BORNE TEST NANTES 2', 'address': 'CREATION STATION TEST NANTES 2', 'position': {'lon': -1.557559, 'lat': 47.195299}, 'banking': 'False', 'bonus': 'False', 'status': 'OPEN', 'contract_name': 'nantes', 'bike_stands': 7, 'available_bike_stands': 6, 'available_bikes': 0, 'last_update': '2024-05-03T10:04:54+00:00'}
Sent message: {'number': 110, 'name': '110-AUDITORIUM', 'address': '1, avenue de Bretagne - REZÉ', 'position': {'lon': -1.554025, 'lat': 47.185402}, 'banking': 'False', 'bonus': 'False', 'status': 'OPEN', 'contract_name': 'nantes', 'bike_stands': 20, 'available_bike_stands': 13, 'available_bikes': 7,

In [9]:
kafka_manager = KafkaManager(KAFKA_BROKER)

# 3. Import des relais
relais_url = "https://data.nantesmetropole.fr/api/explore/v2.1/catalog/datasets/244400404_parcs-relais-nantes-metropole-disponibilites/records?limit=-1"
relais_fields = ["grp_identifiant", "grp_nom", "grp_statut", "grp_disponible", "grp_exploitation", "grp_complet", "grp_horodatage", "idobj", "location", "disponibilite"]
relais_data = fetch_data_from_url(relais_url)
send_data_to_kafka(kafka_manager, "relais", relais_data, relais_fields, expected_type=dict)

# 4. Import des vélos
velos_url = "https://data.nantesmetropole.fr/api/explore/v2.1/catalog/datasets/244400404_stations-velos-libre-service-nantes-metropole-disponibilites/records?limit=100"
velos_fields = ["number", "name", "address", "position", "banking", "bonus", "status", "contract_name", "bike_stands", "available_bike_stands", "available_bikes", "last_update"]
velos_data = fetch_data_from_url(velos_url)
send_data_to_kafka(kafka_manager, "velos", velos_data, velos_fields, expected_type=dict)

kafka_manager.close()

Requesting: https://data.nantesmetropole.fr/api/explore/v2.1/catalog/datasets/244400404_parcs-relais-nantes-metropole-disponibilites/records?limit=-1
Sent message: {'grp_identifiant': '138', 'grp_nom': 'P+R Le Cardo', 'grp_statut': 2, 'grp_disponible': 178, 'grp_exploitation': 206, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:03:41+00:00', 'idobj': '3189', 'location': {'lon': -1.584511976999977, 'lat': 47.262502085999984}, 'disponibilite': 178.0}
Sent message: {'grp_identifiant': '142', 'grp_nom': 'P+R Neustrie 1', 'grp_statut': 2, 'grp_disponible': 744, 'grp_exploitation': 760, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:03:41+00:00', 'idobj': '3558', 'location': {'lon': -1.5924185470000225, 'lat': 47.17707849999999}, 'disponibilite': 744.0}
Sent message: {'grp_identifiant': '143', 'grp_nom': 'P+R Orvault-Morlière', 'grp_statut': 2, 'grp_disponible': 282, 'grp_exploitation': 283, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:03:41+00:00', 'idobj': '3584', 'location':

In [10]:
import time

kafka_manager = KafkaManager(KAFKA_BROKER)

while True:
    # Fetch and send relais data
    relais_data = fetch_data_from_url(relais_url)
    send_data_to_kafka(kafka_manager, "relais", relais_data, relais_fields, expected_type=dict)

    # Fetch and send velos data
    velos_data = fetch_data_from_url(velos_url)
    send_data_to_kafka(kafka_manager, "velos", velos_data, velos_fields, expected_type=dict)

    kafka_manager.flush()

    # Wait for 60 seconds before the next iteration
    time.sleep(60)

Requesting: https://data.nantesmetropole.fr/api/explore/v2.1/catalog/datasets/244400404_parcs-relais-nantes-metropole-disponibilites/records?limit=-1
Sent message: {'grp_identifiant': '138', 'grp_nom': 'P+R Le Cardo', 'grp_statut': 2, 'grp_disponible': 178, 'grp_exploitation': 206, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:03:41+00:00', 'idobj': '3189', 'location': {'lon': -1.584511976999977, 'lat': 47.262502085999984}, 'disponibilite': 178.0}
Sent message: {'grp_identifiant': '142', 'grp_nom': 'P+R Neustrie 1', 'grp_statut': 2, 'grp_disponible': 744, 'grp_exploitation': 760, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:03:41+00:00', 'idobj': '3558', 'location': {'lon': -1.5924185470000225, 'lat': 47.17707849999999}, 'disponibilite': 744.0}
Sent message: {'grp_identifiant': '143', 'grp_nom': 'P+R Orvault-Morlière', 'grp_statut': 2, 'grp_disponible': 282, 'grp_exploitation': 283, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:03:41+00:00', 'idobj': '3584', 'location':

ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relai

Requesting: https://data.nantesmetropole.fr/api/explore/v2.1/catalog/datasets/244400404_parcs-relais-nantes-metropole-disponibilites/records?limit=-1
Sent message: {'grp_identifiant': '138', 'grp_nom': 'P+R Le Cardo', 'grp_statut': 2, 'grp_disponible': 178, 'grp_exploitation': 206, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:03:41+00:00', 'idobj': '3189', 'location': {'lon': -1.584511976999977, 'lat': 47.262502085999984}, 'disponibilite': 178.0}
Sent message: {'grp_identifiant': '142', 'grp_nom': 'P+R Neustrie 1', 'grp_statut': 2, 'grp_disponible': 744, 'grp_exploitation': 760, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:03:41+00:00', 'idobj': '3558', 'location': {'lon': -1.5924185470000225, 'lat': 47.17707849999999}, 'disponibilite': 744.0}
Sent message: {'grp_identifiant': '143', 'grp_nom': 'P+R Orvault-Morlière', 'grp_statut': 2, 'grp_disponible': 282, 'grp_exploitation': 283, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:03:41+00:00', 'idobj': '3584', 'location':

ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAc

Sent message: {'number': 1011, 'name': '01011 - BORNE TEST NANTES 1', 'address': 'Borne test 1', 'position': {'lon': -1.5575, 'lat': 47.19504}, 'banking': 'False', 'bonus': 'False', 'status': 'OPEN', 'contract_name': 'nantes', 'bike_stands': 0, 'available_bike_stands': 0, 'available_bikes': 0, 'last_update': '2022-05-23T14:41:50+00:00'}
Sent message: {'number': 1012, 'name': '01012 - BORNE TEST NANTES 2', 'address': 'CREATION STATION TEST NANTES 2', 'position': {'lon': -1.557559, 'lat': 47.195299}, 'banking': 'False', 'bonus': 'False', 'status': 'OPEN', 'contract_name': 'nantes', 'bike_stands': 7, 'available_bike_stands': 6, 'available_bikes': 0, 'last_update': '2024-05-03T10:04:54+00:00'}
Sent message: {'number': 74, 'name': '074-CANCLAUX', 'address': '8, place Canclaux', 'position': {'lon': -1.57492461719297, 'lat': 47.2143336608893}, 'banking': 'False', 'bonus': 'False', 'status': 'OPEN', 'contract_name': 'nantes', 'bike_stands': 15, 'available_bike_stands': 0, 'available_bikes': 15

...

ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relais : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur relai

Sent message: {'grp_identifiant': '145', 'grp_nom': 'P+R Porte de Vertou 2', 'grp_statut': 2, 'grp_disponible': 727, 'grp_exploitation': 749, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:34:40+00:00', 'idobj': '5532', 'location': {'lon': -1.5047335759999783, 'lat': 47.180079913999975}, 'disponibilite': 727.0}
Sent message: {'grp_identifiant': '137', 'grp_nom': 'P+R Haluchère 2', 'grp_statut': 5, 'grp_disponible': 139, 'grp_exploitation': 155, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:34:40+00:00', 'idobj': '4764', 'location': {'lon': -1.5249751929999888, 'lat': 47.250230052000006}, 'disponibilite': 139.0}
Sent message: {'grp_identifiant': '149', 'grp_nom': 'P+R Marcel Paul', 'grp_statut': 5, 'grp_disponible': 102, 'grp_exploitation': 160, 'grp_complet': 0, 'grp_horodatage': '2025-02-16T18:34:40+00:00', 'idobj': '3776', 'location': {'lon': -1.618008347, 'lat': 47.24590456300001}, 'disponibilite': 102.0}
Sent message: {'grp_identifiant': '155', 'grp_nom': 'P+R Porte de Ver

ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAccumulator is closed
ERROR:root:Erreur lors de l'envoi du message sur velos : RecordAc

Sent message: {'number': 28, 'name': '028-CARRIÈRE MISERY', 'address': 'Rue Joseph Cholet', 'position': {'lon': -1.57990384592236, 'lat': 47.2000724914656}, 'banking': 'False', 'bonus': 'False', 'status': 'OPEN', 'contract_name': 'nantes', 'bike_stands': 16, 'available_bike_stands': 8, 'available_bikes': 8, 'last_update': '2025-01-26T05:11:58+00:00'}
Sent message: {'number': 3, 'name': '003-STRASBOURG', 'address': '4, rue des Carmélites - Place Tirant Lo Blanc', 'position': {'lon': -1.551979, 'lat': 47.21682}, 'banking': 'False', 'bonus': 'False', 'status': 'OPEN', 'contract_name': 'nantes', 'bike_stands': 15, 'available_bike_stands': 15, 'available_bikes': 0, 'last_update': '2025-02-16T18:25:57+00:00'}
Sent message: {'number': 85, 'name': '085-BEL AIR', 'address': '102, rue Paul Bellamy', 'position': {'lon': -1.56002281967663, 'lat': 47.2263944309861}, 'banking': 'False', 'bonus': 'False', 'status': 'OPEN', 'contract_name': 'nantes', 'bike_stands': 14, 'available_bike_stands': 13, 'av

KeyboardInterrupt: 